# PTT5 - common voice finetuning



In [ ]:
# !pip install datasets
# !pip install transformers==4.6.0
# !pip install librosa
# !pip install jiwer
# !pip install pytorch_lightning==1.2.10
# !pip install lightning-bolts
# !pip install neptune-client
# !pip install sentencepiece
# !pip install fairseq

In [ ]:
from datasets import load_dataset, load_metric
from datasets import load_from_disk
import argparse
from datasets import ClassLabel
import random
import pandas as pd
from IPython.display import display, HTML
import re
import json
import IPython.display as ipd
from IPython.display import Audio
import numpy as np
import librosa
import os
import json
import torch
import gc
from torchmetrics.functional import f1
from torchmetrics.functional import accuracy
from dataclasses import dataclass, field
from typing import Any, Callable, Dict, List, NewType, Optional, Tuple, Union
import pytorch_lightning as pl
from torch.utils.data import DataLoader
from pytorch_lightning.loggers.neptune import NeptuneLogger
from fairseq.optim import adafactor

In [ ]:
def show_random_elements(dataset, num_examples=10):
  assert num_examples <= len(dataset), "Can't pick more elements than there are in the dataset."
  picks = []
  for _ in range(num_examples):
      pick = random.randint(0, len(dataset)-1)
      while pick in picks:
          pick = random.randint(0, len(dataset)-1)
      picks.append(pick)

  df = pd.DataFrame(dataset[picks])
  print(df)
  # display(HTML(df.to_html()))

def extract_all_chars(batch):
  all_text = " ".join(batch["sentence"])
  vocab = list(set(all_text))
  return {"vocab": [vocab], "all_text": [all_text]}

def remove_special_characters(batch):
  batch["sentence"] = re.sub(chars_to_ignore_regex, '', batch["sentence"]).lower() + " "
  return batch

# Parâmetros 

In [ ]:
version = "PTT5_noise_oldvocab_adafactor_test7" #@param {type: "string"}
lr = 5e-4#@param {type: "number"}
w_decay = 0#@param {type: "number"}
bs = 4#@param {type: "integer"}
accum_grads = 16#@param {type: "integer"}
patience = 10#@param {type: "integer"}
max_epochs = 100#@param {type: "integer"}
hold_epochs = 1#@param {type: "integer"}

# Define hyperparameters
hparams = {"version": version,
          "lr": lr,
          "w_decay": w_decay,
          "bs": bs,
          "pretrained": 'unicamp-dl/ptt5-base-portuguese-vocab', 
          "patience": patience,
          "hold_epochs":hold_epochs,
          "accum_grads": accum_grads,
          "max_epochs": max_epochs}
hparams

{'accum_grads': 16,
 'bs': 4,
 'hold_epochs': 1,
 'lr': 0.0005,
 'max_epochs': 100,
 'patience': 10,
 'pretrained': 'unicamp-dl/ptt5-base-portuguese-vocab',
 'version': 'PTT5_noise_oldvocab_adafactor_test7',
 'w_decay': 0}

In [ ]:
from google.colab import drive

In [ ]:
drive.mount('/content/drive')

Mounted at /content/drive


## Preprocessed dataset?

In [ ]:
dataset = load_dataset("common_voice", "pt", split="train+validation")

dataset = dataset.train_test_split(test_size=0.15)

common_voice_train = dataset['train']
common_voice_val = dataset['test']

common_voice_test = load_dataset("common_voice", "pt", split="test")

columns_to_remove = ["accent", "age", "client_id", "down_votes", "gender", "locale", "segment", "up_votes"]

common_voice_train = common_voice_train.remove_columns(columns_to_remove)
common_voice_val = common_voice_val.remove_columns(columns_to_remove)
common_voice_test = common_voice_test.remove_columns(columns_to_remove)

Dataset common_voice downloaded and prepared to /root/.cache/huggingface/datasets/common_voice/pt/6.1.0/bb59ce0bb532485ab64b5d488a8dd2addc3104f694e06bcd2c272dc608bb1112. Subsequent calls will reuse this data.


Reusing dataset common_voice (/root/.cache/huggingface/datasets/common_voice/pt/6.1.0/bb59ce0bb532485ab64b5d488a8dd2addc3104f694e06bcd2c272dc608bb1112)


In [ ]:
chars_to_ignore_regex = '[\,\?\.\!\-\;\:\"\“\%\‘\”\�]'

common_voice_train = common_voice_train.map(remove_special_characters)
common_voice_val = common_voice_val.map(remove_special_characters)
common_voice_test = common_voice_test.map(remove_special_characters)

show_random_elements(common_voice_train)


                                                path                                           sentence
0  /root/.cache/huggingface/datasets/downloads/ex...  ele tentou em vão estabelecer um relacionament...
1  /root/.cache/huggingface/datasets/downloads/ex...              joão e gustavo não passaram no teste 
2  /root/.cache/huggingface/datasets/downloads/ex...       as visitas não poderiam imaginar a surpresa 
3  /root/.cache/huggingface/datasets/downloads/ex...                                     ok não é isso 
4  /root/.cache/huggingface/datasets/downloads/ex...  dois policiais vestindo coletes fluorescentes ...
5  /root/.cache/huggingface/datasets/downloads/ex...                           um casal andando na rua 
6  /root/.cache/huggingface/datasets/downloads/ex...                         muro da corte legislativa 
7  /root/.cache/huggingface/datasets/downloads/ex...  duas crianças dentro de uma casa de pé sobre m...
8  /root/.cache/huggingface/datasets/downloads/ex...           

In [ ]:
from transformers import T5Tokenizer
from transformers import T5Model, T5ForConditionalGeneration

print(hparams["pretrained"])

unicamp-dl/ptt5-base-portuguese-vocab


In [ ]:
tokenizer = T5Tokenizer.from_pretrained(hparams["pretrained"])

model_pt = T5ForConditionalGeneration.from_pretrained(hparams["pretrained"])

In [ ]:
print(common_voice_train)
print(common_voice_train[0])

Dataset({
    features: ['path', 'sentence'],
    num_rows: 9440
})
{'path': '/root/.cache/huggingface/datasets/downloads/extracted/55c28abb37e427173e7a85b9464355d86111a072367ba97d8a00ef5b45f14eeb/cv-corpus-6.1-2020-12-11/pt/clips/common_voice_pt_20347433.mp3', 'sentence': 'e eu sou o maior do lote '}


In [ ]:
print(common_voice_val)
print(common_voice_val[0])

Dataset({
    features: ['path', 'sentence'],
    num_rows: 1666
})
{'path': '/root/.cache/huggingface/datasets/downloads/extracted/55c28abb37e427173e7a85b9464355d86111a072367ba97d8a00ef5b45f14eeb/cv-corpus-6.1-2020-12-11/pt/clips/common_voice_pt_20523634.mp3', 'sentence': 'talvez tenha sido ontem '}


In [ ]:
print(common_voice_test)
print(common_voice_test[0])

Dataset({
    features: ['path', 'sentence'],
    num_rows: 4641
})
{'path': '/root/.cache/huggingface/datasets/downloads/extracted/55c28abb37e427173e7a85b9464355d86111a072367ba97d8a00ef5b45f14eeb/cv-corpus-6.1-2020-12-11/pt/clips/common_voice_pt_21832853.mp3', 'sentence': 'nem o radar nem os outros instrumentos detectaram o bombardeiro stealth '}


In [ ]:
common_voice_train['sentence']

['e eu sou o maior do lote ',
 'e é melhor eu ler seus livros disse o garoto ',
 'que filmes estão tocando no cinema mais próximo ',
 'o dia está quente ',
 'tradução de texto ',
 'quando a panela esfriara o monge e o menino olhavam para ela ofuscados ',
 'eu posso explicar se você apenas escutar ',
 'é um dos nossos ',
 'ele vestiu sua roupa árabe de linho branco comprou especialmente para este dia ',
 'levantou algumas vacas ',
 'dois homens usando capacetes para motociclistas um carregando um pedaço de papel ',
 'eles tinham muito a divulgar ',
 'eu suponho que tudo isso está levando a algum lugar ',
 'o que você sabe sobre isso ',
 'mas ela não disse nada ',
 'as maçãs vendidas lá são realmente deliciosas ',
 'abra o google music e reproduza tudo ',
 'este artigo é dedicado à querida vovó ',
 'quatro crianças estão fazendo uma ponte de ginástica nas mãos e nos pés ',
 'é conveniente manter algum dinheiro ',
 'eu vejo o que você quer dizer ',
 'homem com o pico das viúvas que alcang

In [ ]:
import re

SPACE_NORMALIZER = re.compile(r"\s+")

def tokenize_line(line):
    line = SPACE_NORMALIZER.sub(" ", line)
    line = line.strip()
    return line.split()

In [ ]:
common_dataset = common_voice_train['sentence'] + common_voice_val['sentence'] + common_voice_test['sentence']

print(common_dataset)

common_dataset = ' '.join(common_dataset)

print(common_dataset)

common_dataset = tokenize_line(common_dataset)

print(common_dataset)

['e eu sou o maior do lote ', 'e é melhor eu ler seus livros disse o garoto ', 'que filmes estão tocando no cinema mais próximo ', 'o dia está quente ', 'tradução de texto ', 'quando a panela esfriara o monge e o menino olhavam para ela ofuscados ', 'eu posso explicar se você apenas escutar ', 'é um dos nossos ', 'ele vestiu sua roupa árabe de linho branco comprou especialmente para este dia ', 'levantou algumas vacas ', 'dois homens usando capacetes para motociclistas um carregando um pedaço de papel ', 'eles tinham muito a divulgar ', 'eu suponho que tudo isso está levando a algum lugar ', 'o que você sabe sobre isso ', 'mas ela não disse nada ', 'as maçãs vendidas lá são realmente deliciosas ', 'abra o google music e reproduza tudo ', 'este artigo é dedicado à querida vovó ', 'quatro crianças estão fazendo uma ponte de ginástica nas mãos e nos pés ', 'é conveniente manter algum dinheiro ', 'eu vejo o que você quer dizer ', 'homem com o pico das viúvas que alcanga acima da face da ro

In [ ]:
vocab_common = list(set(common_dataset))

print(len(vocab_common))

print(vocab_common)

13708
['estação', 'esmagando', 'erradas', 'assoalho', 'brilhou', 'anexo', 'recuperado', 'estraga', 'articulação', 'discutiu', 'plantações', 'cangurus', 'despertada', 'encontrou', 'procurando', 'barril', 'outra', 'reparado', 'platéia', 'vou', 'cristal', 'nada', 'hopkins', 'pequim', 'patins', 'house', 'vai', 'sebes', 'examinada', 'montadas', 'prometer', 'causar', 'fico', 'indicações', 'conseguiria', 'drogas', 'segundafeira', 'radiador', 'desativar', 'chrome', 'continuava', 'dançarina', 'convite', 'seguida', 'elástico', 'iremos', 'contam', 'esculpida', 'meiofio', 'pianoforte', 'multado', 'automáticos', 'tux', 'grátis', 'grau', 'recémcasado', 'reencha', 'arquivo', 'incentivo', 'mente', 'morna', 'oficialmente', 'puxeo', 'protocolos', 'juros', 'navegar', 'fechadas', 'artefatos', 'examina', 'pendura', 'trilhos', 'deles', 'contribuem', 'atualmente', 'garçom', 'rompeu', 'padre', 'terence', 'surpreende', 'desembaralhar', 'tempestades', 'pátria', 'superfícies', 'floaties', 'neles', 'se', 'orienta

In [ ]:
vocab_bert_timbau = list(tokenizer.get_vocab().keys())

print(vocab_bert_timbau)

['<pad>', '</s>', '<unk>', ',', '▁de', '.', 's', '▁a', '▁e', '▁o', '▁do', '▁da', '▁em', '▁que', '-', '▁"', '▁um', '▁uma', '▁com', '▁no', '▁para', '▁é', '▁na', '▁foi', '▁(', '▁A', '▁por', '"', '▁O', '▁como', '▁os', '▁', 'se', 'r', '▁dos', '▁se', ')', '▁ao', '▁sua', '▁mais', '▁Em', 'm', '▁as', 'o', 'a', '▁seu', ':', '▁não', '▁à', '",', '▁pela', '▁das', '▁ou', 'do', '▁pelo', '▁também', 'u', '▁ser', 'da', 'ndo', '▁entre', 'e', '▁são', '),', '".', '▁anos', '▁No', '▁era', '▁ele', '▁mas', '▁foram', 't', '▁cidade', ').', ';', '▁até', 'i', 'l', '▁-', 'es', '▁seus', '▁sobre', 'va', '▁onde', '▁nos', '▁Os', 'de', '▁tem', '▁ano', 'A', '▁primeiro', '▁Na', '▁parte', 'ção', '▁quando', '▁sendo', 'n', 'ia', 'ram', '▁São', '▁primeira', '▁mesmo', 'na', 'y', 'la', 'mente', '▁dois', '▁dia', '▁durante', '▁km', "'", '▁1', '▁Brasil', '/', '▁depois', '▁re', '▁I', '▁nas', '▁De', 'ra', 'd', 'ta', '▁Foi', 'to', 'lo', '▁suas', '▁nome', '▁2', '▁Ele', '▁outros', '▁E', 'em', '▁contra', 'is', '▁grande', '▁3', '▁ainda',

In [ ]:
vocab_common_diff = list(set(vocab_common).difference(vocab_bert_timbau))
print(vocab_common_diff)

print(len(vocab_common_diff))

['estação', 'esmagando', 'erradas', 'assoalho', 'brilhou', 'anexo', 'recuperado', 'estraga', 'articulação', 'discutiu', 'plantações', 'cangurus', 'despertada', 'encontrou', 'procurando', 'barril', 'outra', 'reparado', 'platéia', 'cristal', 'hopkins', 'pequim', 'patins', 'vai', 'sebes', 'examinada', 'montadas', 'prometer', 'causar', 'indicações', 'conseguiria', 'drogas', 'segundafeira', 'radiador', 'desativar', 'chrome', 'continuava', 'dançarina', 'convite', 'seguida', 'elástico', 'iremos', 'contam', 'esculpida', 'meiofio', 'pianoforte', 'multado', 'automáticos', 'tux', 'grátis', 'grau', 'recémcasado', 'reencha', 'arquivo', 'incentivo', 'morna', 'puxeo', 'protocolos', 'juros', 'navegar', 'fechadas', 'artefatos', 'examina', 'pendura', 'trilhos', 'deles', 'contribuem', 'garçom', 'rompeu', 'padre', 'terence', 'surpreende', 'desembaralhar', 'tempestades', 'pátria', 'superfícies', 'floaties', 'neles', 'oriental', 'madison', 'pierre', 'tiver', 'possessividade', 'fez', 'óperas', 'transmite', '

In [ ]:
# print(len(tokenizer))  

# for word in vocab_common_diff:
#   tokenizer.add_tokens([word])

# print(len(tokenizer))

In [ ]:
tokenizer

PreTrainedTokenizer(name_or_path='unicamp-dl/ptt5-base-portuguese-vocab', vocab_size=32100, model_max_len=1000000000000000019884624838656, is_fast=False, padding_side='right', special_tokens={'eos_token': '</s>', 'unk_token': '<unk>', 'pad_token': '<pad>', 'additional_special_tokens': ['<extra_id_0>', '<extra_id_1>', '<extra_id_2>', '<extra_id_3>', '<extra_id_4>', '<extra_id_5>', '<extra_id_6>', '<extra_id_7>', '<extra_id_8>', '<extra_id_9>', '<extra_id_10>', '<extra_id_11>', '<extra_id_12>', '<extra_id_13>', '<extra_id_14>', '<extra_id_15>', '<extra_id_16>', '<extra_id_17>', '<extra_id_18>', '<extra_id_19>', '<extra_id_20>', '<extra_id_21>', '<extra_id_22>', '<extra_id_23>', '<extra_id_24>', '<extra_id_25>', '<extra_id_26>', '<extra_id_27>', '<extra_id_28>', '<extra_id_29>', '<extra_id_30>', '<extra_id_31>', '<extra_id_32>', '<extra_id_33>', '<extra_id_34>', '<extra_id_35>', '<extra_id_36>', '<extra_id_37>', '<extra_id_38>', '<extra_id_39>', '<extra_id_40>', '<extra_id_41>', '<extra_i

In [ ]:
sent = "várias essoas em uma quadra de basquete"

print(tokenizer.tokenize(sent))

input_ids = tokenizer.encode(sent, return_tensors='pt')
print(input_ids)

print(len(input_ids[0]))

print(tokenize_line(sent))

['▁várias', '▁e', 'sso', 'as', '▁em', '▁uma', '▁quadra', '▁de', '▁basquete']
tensor([[ 367,    8, 1570,  397,   12,   17, 6382,    4, 7339,    1]])
10
['várias', 'essoas', 'em', 'uma', 'quadra', 'de', 'basquete']


In [ ]:
# sent = "várias essoas em uma quadra de basquete"

print(tokenizer.tokenize(sent))

print(tokenize_line(sent))

input_ids1 = tokenizer.encode(tokenize_line(sent), is_split_into_words =True, return_tensors='pt')
print('input_ids1:', input_ids1)

input_ids2 = tokenizer.encode(sent, return_tensors='pt')
print('input_ids2:', input_ids2)

print(len(input_ids1[0]))
print(len(input_ids2[0]))

for word in input_ids1[0]:
  print(tokenizer.decode(word))

for word in input_ids2[0]:
  print(tokenizer.decode(word))

['▁várias', '▁e', 'sso', 'as', '▁em', '▁uma', '▁quadra', '▁de', '▁basquete']
['várias', 'essoas', 'em', 'uma', 'quadra', 'de', 'basquete']
input_ids1: tensor([[ 367,    8, 1570,  397,   12,   17, 6382,    4, 7339,    1]])
input_ids2: tensor([[ 367,    8, 1570,  397,   12,   17, 6382,    4, 7339,    1]])
10
10
várias
e
sso
as
em
uma
quadra
de
basquete
</s>
várias
e
sso
as
em
uma
quadra
de
basquete
</s>


In [ ]:
print(tokenizer.eos_token_id)

1


In [ ]:
# sample_outputs = _generate_tokens(input_ids)

# print("Output:\n" + 100 * '-')
# for i, sample_output in enumerate(sample_outputs):
#   print("{}: {}".format(i, tokenizer.decode(sample_output, skip_special_tokens=True)))

In [ ]:
print(input_ids1.shape)

print(input_ids1)

torch.Size([1, 10])
tensor([[ 367,    8, 1570,  397,   12,   17, 6382,    4, 7339,    1]])


In [ ]:
print(tokenizer.all_special_ids)
print(tokenizer.all_special_tokens)

print(tokenizer.mask_token)

print(len(tokenizer))

print(tokenizer.all_special_tokens[3:])

Using mask_token, but it is not set yet.


[1, 2, 0, 32099, 32098, 32097, 32096, 32095, 32094, 32093, 32092, 32091, 32090, 32089, 32088, 32087, 32086, 32085, 32084, 32083, 32082, 32081, 32080, 32079, 32078, 32077, 32076, 32075, 32074, 32073, 32072, 32071, 32070, 32069, 32068, 32067, 32066, 32065, 32064, 32063, 32062, 32061, 32060, 32059, 32058, 32057, 32056, 32055, 32054, 32053, 32052, 32051, 32050, 32049, 32048, 32047, 32046, 32045, 32044, 32043, 32042, 32041, 32040, 32039, 32038, 32037, 32036, 32035, 32034, 32033, 32032, 32031, 32030, 32029, 32028, 32027, 32026, 32025, 32024, 32023, 32022, 32021, 32020, 32019, 32018, 32017, 32016, 32015, 32014, 32013, 32012, 32011, 32010, 32009, 32008, 32007, 32006, 32005, 32004, 32003, 32002, 32001, 32000]
['</s>', '<unk>', '<pad>', '<extra_id_0>', '<extra_id_1>', '<extra_id_2>', '<extra_id_3>', '<extra_id_4>', '<extra_id_5>', '<extra_id_6>', '<extra_id_7>', '<extra_id_8>', '<extra_id_9>', '<extra_id_10>', '<extra_id_11>', '<extra_id_12>', '<extra_id_13>', '<extra_id_14>', '<extra_id_15>', '

In [ ]:
# special_tokens_dict = {'mask_token': '<MASK>'}
# tokenizer.add_special_tokens(special_tokens_dict)

print(tokenizer.get_special_tokens_mask([32099, 32098, 32097, 32096, 32095, 32094, 32093, 32092, 32091, 32090, 32089, 32088, 32087, 32086, 32085, 32084, 32083, 32082, 32081, 32080, 32079, 32078, 32077, 32076, 32075, 32074, 32073, 32072, 32071, 32070, 32069, 32068, 32067, 32066, 32065, 32064, 32063, 32062, 32061, 32060, 32059, 32058, 32057, 32056, 32055, 32054, 32053, 32052, 32051, 32050, 32049, 32048, 32047, 32046, 32045, 32044, 32043, 32042, 32041, 32040, 32039, 32038, 32037, 32036, 32035, 32034, 32033, 32032, 32031, 32030, 32029, 32028, 32027, 32026, 32025, 32024, 32023, 32022, 32021, 32020, 32019, 32018, 32017, 32016, 32015, 32014, 32013, 32012, 32011, 32010, 32009, 32008, 32007, 32006, 32005, 32004, 32003, 32002, 32001, 32000]))

print(tokenizer.all_special_ids)
print(tokenizer.all_special_tokens)
tokenizer.sanitize_special_tokens()

print(len(tokenizer))

[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1]
[1, 2, 0, 32099, 32098, 32097, 32096, 32095, 32094, 32093, 32092, 32091, 32090, 32089, 32088, 32087, 32086, 32085, 32084, 32083, 32082, 32081, 32080, 32079, 32078, 32077, 32076, 32075, 32074, 32073, 32072, 32071, 32070, 32069, 32068, 32067, 32066, 32065, 32064, 32063, 32062, 32061, 32060, 32059, 32058, 32057, 32056, 32055, 32054, 32053, 32052, 32051, 32050, 32049, 32048, 32047, 32046, 32045, 32044, 32043, 32042, 32041, 32040, 32039, 32038, 32037, 32036, 32035, 32034, 32033, 32032, 32031, 32030, 32029, 32028, 32027, 32026, 32025, 32024, 32023, 32022, 32021, 32020, 32019, 32018, 32017, 32016, 32015, 32014, 32013, 32012, 32011, 32010, 32009, 32008, 32007, 32006, 32005, 32004, 32003, 32002, 

In [ ]:
tokenizer

PreTrainedTokenizer(name_or_path='unicamp-dl/ptt5-base-portuguese-vocab', vocab_size=32100, model_max_len=1000000000000000019884624838656, is_fast=False, padding_side='right', special_tokens={'eos_token': '</s>', 'unk_token': '<unk>', 'pad_token': '<pad>', 'additional_special_tokens': ['<extra_id_0>', '<extra_id_1>', '<extra_id_2>', '<extra_id_3>', '<extra_id_4>', '<extra_id_5>', '<extra_id_6>', '<extra_id_7>', '<extra_id_8>', '<extra_id_9>', '<extra_id_10>', '<extra_id_11>', '<extra_id_12>', '<extra_id_13>', '<extra_id_14>', '<extra_id_15>', '<extra_id_16>', '<extra_id_17>', '<extra_id_18>', '<extra_id_19>', '<extra_id_20>', '<extra_id_21>', '<extra_id_22>', '<extra_id_23>', '<extra_id_24>', '<extra_id_25>', '<extra_id_26>', '<extra_id_27>', '<extra_id_28>', '<extra_id_29>', '<extra_id_30>', '<extra_id_31>', '<extra_id_32>', '<extra_id_33>', '<extra_id_34>', '<extra_id_35>', '<extra_id_36>', '<extra_id_37>', '<extra_id_38>', '<extra_id_39>', '<extra_id_40>', '<extra_id_41>', '<extra_i

In [ ]:
sample_outputs = model_pt.generate(
    input_ids1,
    do_sample=True, 
    max_length=len(input_ids[0])+1, 
    top_k=100, 
    top_p=0.95, 
    num_return_sequences=5,
    length_penalty=0.4,
    repetition_penalty=0.4,
    pad_token_id=0,
    eos_token_id=1,
    early_stopping=True
)

beam_outputs = model_pt.generate(
              input_ids1,  
              num_beams=500, 
              temperature=0.5,
              no_repeat_ngram_size=0, 
              num_return_sequences=5,
              length_penalty=0.8,
              repetition_penalty=0.8,
              num_beam_groups=5,
              pad_token_id=0,
              eos_token_id=1,
              early_stopping=True
          )


print("Output:\n" + 100 * '-')
for i, sample_output in enumerate(sample_outputs):
  print("{}: {}".format(i, tokenizer.decode(sample_output, skip_special_tokens=True)))

print("Output:\n" + 100 * '-')
for i, sample_output in enumerate(beam_outputs):
  print("{}: {}".format(i, tokenizer.decode(sample_output, skip_special_tokens=True)))

/usr/local/lib/python3.7/dist-packages/transformers/generation_beam_search.py:197: UserWarning: Passing `max_length` to BeamSearchScorer is deprecated and has no effect.`max_length` should be passed directly to `beam_search(...)`, `beam_sample(...)`,or `group_beam_search(...)`.
  "Passing `max_length` to BeamSearchScorer is deprecated and has no effect."
/usr/local/lib/python3.7/dist-packages/torch/_tensor.py:575: UserWarning: floor_divide is deprecated, and will be removed in a future version of pytorch. It currently rounds toward 0 (like the 'trunc' function NOT 'floor'). This results in incorrect rounding for negative values.
To keep the current behavior, use torch.div(a, b, rounding_mode='trunc'), or for actual floor division, use torch.div(a, b, rounding_mode='floor'). (Triggered internally at  /pytorch/aten/src/ATen/native/BinaryOps.cpp:467.)
  return torch.floor_divide(self, other)


Output:
----------------------------------------------------------------------------------------------------
0: várias essoas em uma quadra e basquete e
1: várias essoas em uma quadra de basquete de
2: várias essoas em uma quadra de basquete de
3: várias essoas em uma quadra de basquete de
4: várias essoas em uma quadra de basquete
Output:
----------------------------------------------------------------------------------------------------
0: várias essoas em uma quadra de basquete
1: várias essoas em uma quadra de basquete
2: várias essoas em uma quadra de basquete
3: várias essoas em uma quadra de basquete
4: várias essoas em uma quadra de basquete


# Datasets and Dataloaders

In [ ]:
neptune_logger = NeptuneLogger(
    api_key="eyJhcGlfYWRkcmVzcyI6Imh0dHBzOi8vYXBwLm5lcHR1bmUuYWkiLCJhcGlfdXJsIjoiaHR0cHM6Ly9hcHAubmVwdHVuZS5haSIsImFwaV9rZXkiOiJjMmJkZTg1Yy1kMjQ1LTRmMjEtYjBmYy1kMjVlMmMxODcyMTgifQ==",
    project_name='orllem/PTseq2seq')

NeptuneLogger will work in online mode


In [ ]:
from transformers.data.data_collator import DataCollatorForSeq2Seq 

collate_fn=DataCollatorForSeq2Seq(tokenizer=tokenizer,
                                  model=model_pt,
                                  padding='longest',
                                  # max_length=512,
                                  label_pad_token_id=-100,
                                             )

In [ ]:
from string import ascii_letters

def random_bool(probability=0.5):
    """Returns True with given probability
    Args:
        probability: probability to return True
    """
    assert (0 <= probability <= 1), "probability needs to be >= 0 and <= 1"
    return random.random() < probability

def delete_random_token(line, probability):
    """Delete random tokens in a given String with given probability
    Args:
        line: a String
        probability: probability to delete each token
    """
    line_split = list(line)
    # line_split = line.split()
    # print(line_split)
    ret = []
    for token in line_split:
        if token==' ':
            ret.append(token)
        elif not random_bool(probability):
            ret.append(token)
    return "".join(ret)


def replace_random_token(line, probability):
    """Replace random tokens in a String by a filler token with given probability
    Args:
        line: a String
        probability: probability to replace each token
        filler_token: token replacing chosen tokens
    """
    # line_split = line.split()
    line_split = list(line)
    # print(line_split)
    for i in range(len(line_split)):
        if line_split[i]!=' ':
            if random_bool(probability):
                line_split[i] = random.choice(ascii_letters)
    return "".join(line_split)

In [ ]:
class AudioDataset(torch.utils.data.Dataset):

  def __init__(self, common_voice, transform=None):
    self.common_voice = common_voice
    self.transform = transform

  def __len__(self):
    return len(self.common_voice)

  def __getitem__(self, idx):
    
    batch = self.common_voice[idx]

    sent = batch['sentence']
    noise_sent =  batch['sentence']
    noise_sent = delete_random_token(noise_sent, 0.05)
    noise_sent = replace_random_token(noise_sent, 0.08)

    # data = tokenizer(target)
    data_label = tokenizer(sent)
    data = tokenizer(noise_sent)
    data["labels"] = data_label["input_ids"]  
    return data

In [ ]:
train_dataset = AudioDataset(common_voice_train)
val_dataset = AudioDataset(common_voice_val)
test_dataset = AudioDataset(common_voice_test)

In [ ]:
print('Número de amostras de trenamento:', len(train_dataset))
print('Número de amostras de validação:', len(val_dataset))
print('Número de amostras de teste:', len(test_dataset))

Número de amostras de trenamento: 9440
Número de amostras de validação: 1666
Número de amostras de teste: 4641


In [ ]:
data = train_dataset[0]

print('data:', data)

data: {'input_ids': [8, 1283, 10270, 4790, 153, 10, 3831, 146, 1], 'attention_mask': [1, 1, 1, 1, 1, 1, 1, 1, 1], 'labels': [8, 2077, 10270, 9, 153, 10, 9942, 1]}


In [ ]:
batch_size = hparams["bs"]

train_dataloader = DataLoader(train_dataset, batch_size=batch_size,
                              collate_fn = collate_fn,
                              shuffle=True, num_workers=4)
val_dataloader = DataLoader(val_dataset, batch_size=batch_size,
                            collate_fn = collate_fn,
                            shuffle=False,  num_workers=4)
test_dataloader = DataLoader(test_dataset, batch_size=batch_size,
                             collate_fn = collate_fn,
                             shuffle=False,  num_workers=4)

print('Número de minibatches de trenamento:', len(train_dataloader))
print('Número de minibatches de validação:', len(val_dataloader))
print('Número de minibatches de teste:', len(test_dataloader))

batch = next(iter(train_dataloader))
print(batch)
# x_train, y_train = next(iter(train_dataloader))
x_train, y_train = batch['input_ids'], batch['labels']
print("\nDimensões dos dados de um minibatch:", x_train.size())
print("\nDimensões dos dados de um minibatch:", y_train.size())

batch = next(iter(val_dataloader))
print("\nDimensões dos dados de um minibatch val:", batch['input_ids'].size())

batch = next(iter(test_dataloader))
print("\nDimensões dos dados de um minibatch test:", batch['input_ids'].size())

print("Valores mínimo e máximo: ", torch.min(x_train), torch.max(x_train))
print("Valores mínimo e máximo: ", torch.min(y_train), torch.max(y_train))
print("Tipo dos dados:         ", type(x_train))
print("Tipo das classes:       ", type(y_train))

Número de minibatches de trenamento: 2360
Número de minibatches de validação: 417
Número de minibatches de teste: 1161
{'input_ids': tensor([[   68,     7,  2532,   689,    13,    16,   731,    96,  1020,  1442,
          1500,  6152,    96,  1454,    21,  2890,    77,     1,     0,     0,
             0,     0,     0],
        [ 1932,   589,     9,    31,  2128,    89,    61, 15744,    18,   643,
           408,    76,  4717,     1,     0,     0,     0,     0,     0,     0,
             0,     0,     0],
        [ 4149,   352,   878,  2818,  4565,     7,   189,  3017,     9,   781,
            43,    44,   956,   226,  5111,  1556,   617,  2468,     6,  1709,
             4,    77,     1],
        [   16,   878,    31,     6,    41,   656,  5715,  1751, 16473,  3946,
          2089,     1,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0, 0],
        [1, 

In [ ]:
for input_ids, labels in zip(batch['input_ids'], batch['labels']):
  print(input_ids)
  print(tokenizer.decode(input_ids))
  print(labels)
  print(tokenizer.decode(labels[labels!=-100]))
  # print(tokenizer.decode(labels, skip_special_tokens=True))
  print('-------------------------')

tensor([ 1162,     9, 14224,  1162,    30,   129,   164,     6,  3060,   601,
          695, 14979,   197,     9,  4512,  1512,   388,  2719,    31,   652,
         2726,   537,     1])
nem o radar nem os outros insrumvotos detectaram o bombardPiro stRath</s>
tensor([ 1162,     9, 14224,  1162,    30,   129,  3487, 14979,   197,     9,
         4512,  1512,  1406,    31,  1785,   329,   537,     1])
nem o radar nem os outros instrumentos detectaram o bombardeiro stealth</s>
-------------------------
tensor([8577, 1708,    8,  209,   33,   41,    6, 1423,  241,  248,   11, 2886,
           1,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0])
pedir dinheiro eprmstado às pessoas da aldeia</s> <pad> <pad> <pad> <pad> <pad> <pad> <pad> <pad> <pad> <pad>
tensor([8577, 1708, 7491,  241,  248,   11, 2886,    1, -100, -100, -100, -100,
        -100, -100, -100, -100, -100, -100])
pedir dinheiro emprestado às pessoas da aldeia</s>
-------------------------
tensor([1141,    1,    0,   

In [ ]:
# print(batch['attention_mask'].shape)
# print(batch['token_type_ids'].shape)

# Creating the lightning module

In [ ]:
from pl_bolts.optimizers.lr_scheduler import LinearWarmupCosineAnnealingLR

In [ ]:
import collections

def normalize_answer(s):
    """Lower text and remove extra whitespace."""

    def white_space_fix(text):
        return ' '.join(text.split())

    def lower(text):
        return text.lower()

    return white_space_fix(lower(s))

def get_tokens(s):
    if not s: return []
    return normalize_answer(s).split()

def compute_exact(a_gold, a_pred):
    return int(normalize_answer(a_gold) == normalize_answer(a_pred))

def compute_f1(a_gold, a_pred):
    gold_toks = get_tokens(a_gold)
    pred_toks = get_tokens(a_pred)
    common = collections.Counter(gold_toks) & collections.Counter(pred_toks)
    num_same = sum(common.values())
    if len(gold_toks) == 0 or len(pred_toks) == 0:
        # If either is no-answer, then F1 is 1 if they agree, 0 otherwise
        return int(gold_toks == pred_toks)
    if num_same == 0:
        return 0
    precision = 1.0 * num_same / len(pred_toks)
    recall = 1.0 * num_same / len(gold_toks)
    f1 = (2 * precision * recall) / (precision + recall)
    return f1

In [ ]:
class PTT5Net(pl.LightningModule):
    def __init__(self, *args, **kwargs):
        super().__init__()

        self.hparams = hparams

        # Note como a arquitetura esta dependente dos hiperparâmetros salvos.
        self.model = model_pt

        # for param in self.model.bert.parameters():
        #     param.requires_grad = False

        self.tokenizer = tokenizer

    def forward(self, input_values):
        logits = self.model(**input_values).prediction_logits
        return logits

    def predict_step(self, batch, batch_idx, dataloader_idx=None, gen_type=None):
        
        target = batch["labels"]

        if gen_type==0:
          # normal beam search generation  
          pred_tokens = self._generate_tokens(batch["input_ids"])
        elif gen_type==1:
          # fast beam search generation
          pred_tokens = self._fast_generate_tokens(batch["input_ids"])  
        elif gen_type==2:
          # Top-K Sampling  generation
          pred_tokens = self._topK_generate_tokens(batch["input_ids"])  
        elif gen_type==3:   
          # Top-p generation
          pred_tokens = self._topp_generate_tokens(batch["input_ids"]) 
        elif gen_type==4:  
          # # Top-p e Top-K Sampling generation
          pred_tokens = self._toppK_generate_tokens(batch["input_ids"]) 
        else:
          pred_tokens = self._greedy_generate_tokens(batch["input_ids"])

        # Tokens -> String
        decoded_pred = self.tokenizer.batch_decode(pred_tokens, skip_special_tokens=True)
        decoded_target = [self.tokenizer.decode(tokens[tokens!=-100], skip_special_tokens=True) for tokens in target] 
        

        print(f"\nSample Target: {decoded_target[0]}\nPrediction: {decoded_pred[0]}\n")

        return decoded_pred, decoded_target   
    
    def _greedy_generate_tokens(self, input_ids):
        
        decoded_ids = self.model.generate(
            input_ids, 
            # max_length=512,
            max_length=input_ids.shape[1]+1, 
            # pad_token_id=0,
            # eos_token_id=1,
            # early_stopping=True
        )


        return decoded_ids

    def _fast_generate_tokens(self, input_ids):
        '''
        Token generation
        '''
          
        # print(input_ids.shape)
        decoded_ids = self.model.generate(
            input_ids, 
            max_length=input_ids.shape[1]+1, 
            num_beams=5, 
            temperature=0.1,
            no_repeat_ngram_size=2, 
            num_return_sequences=1,
            length_penalty=0.8,
            repetition_penalty=0.8,
            num_beam_groups=5,
            pad_token_id=0,
            eos_token_id=1,
            early_stopping=True
        )

        return decoded_ids   
    
    def _generate_tokens(self, input_ids):
        '''
        Token generation
        '''
          
        # print(input_ids.shape)
        decoded_ids = self.model.cpu().generate(
            input_ids, 
            max_length=input_ids.shape[1]+1, 
            num_beams=500, 
            temperature=0.1,
            no_repeat_ngram_size=2, 
            num_return_sequences=1,
            length_penalty=0.8,
            repetition_penalty=0.8,
            num_beam_groups=5,
            pad_token_id=0,
            eos_token_id=1,
            early_stopping=True
        )

        return decoded_ids   
    
    def _topK_generate_tokens(self, input_ids):
        '''
        Token TopK generation
        '''
          
        # print(input_ids.shape)
        decoded_ids = self.model.generate(
            input_ids, 
            max_length=input_ids.shape[1]+1, 
            do_sample=True,  
            top_k=500, 
            temperature=0.1,
            num_return_sequences=1,
            length_penalty=0.8,
            repetition_penalty=0.8,
            pad_token_id=0,
            eos_token_id=1,
            early_stopping=True
        )

        return decoded_ids
    
    def _topp_generate_tokens(self, input_ids):
        '''
        Token TopK generation
        '''
          
        # print(input_ids.shape)
        decoded_ids = self.model.generate(
            input_ids, 
            max_length=input_ids.shape[1]+1, 
            do_sample=True,  
            top_p=0.92, 
            top_k=0,
            temperature=0.1,
            num_return_sequences=1,
            length_penalty=0.8,
            repetition_penalty=0.8,
            pad_token_id=0,
            eos_token_id=1,
            early_stopping=True
        )

        return decoded_ids
    
    def _toppK_generate_tokens(self, input_ids):
        '''
        Token TopK generation
        '''
          
        # print(input_ids.shape)
        decoded_ids = self.model.generate(
            input_ids, 
            max_length=input_ids.shape[1]+1, 
            do_sample=True,  
            top_p=0.95, 
            top_k=50,
            temperature=0.1,
            num_return_sequences=1,
            length_penalty=0.8,
            repetition_penalty=0.8,
            pad_token_id=0,
            eos_token_id=1,
            early_stopping=True
        )

        return decoded_ids

    def training_step(self, train_batch, batch_idx):
        # loss compute
        loss = self.model(**train_batch).loss
        # print('loss', loss)

        self.log('cross_loss_step', loss, on_step=True, prog_bar=True)
        
        return loss

    def training_epoch_end(self, outputs):
        loss = torch.stack([x['loss'] for x in outputs]).mean()       

        self.log("train_loss", loss, prog_bar=True)
  
    def validation_step(self, val_batch, batch_idx):

        # predict 
        target = val_batch["labels"]
        val_loss = self.model(**val_batch).loss

        # pred_tokens = self._fast_generate_tokens(val_batch["input_ids"])
        pred_tokens = self._greedy_generate_tokens(val_batch["input_ids"])
        # Tokens -> String
        # decoded_pred = [self.tokenizer.decode(tokens, skip_special_tokens=True) for tokens in pred_tokens]
        decoded_pred = self.tokenizer.batch_decode(pred_tokens, skip_special_tokens=True)
        
        decoded_target = [self.tokenizer.decode(tokens[tokens!=-100], skip_special_tokens=True) for tokens in target]
        return {"val_loss_step": val_loss, "pred": decoded_pred, "target": decoded_target}

    def validation_epoch_end(self, outputs):
        val_loss = torch.stack([x['val_loss_step'] for x in outputs]).mean()
        trues = sum([list(x['target']) for x in outputs], [])
        preds = sum([list(x['pred']) for x in outputs], [])
        
        n = random.choices(range(len(trues)), k=2)
        for i in n:
          print(f"\nSample Target: {trues[i]}\nPrediction: {preds[i]}\n")
        
        f1 = []
        for true, pred in zip(trues, preds):
            f1.append(compute_f1(a_gold=true, a_pred=pred))
        f1_val = np.mean(f1)


        self.log("val_loss", val_loss, prog_bar=True)
        self.log("val_f1", f1_val, prog_bar=True)
  
    def test_step(self, test_batch, batch_idx):
        
        # input_values, labels = test_batch['input_values'], test_batch['labels']
        target = test_batch["labels"]
        test_loss = self.model(**test_batch).loss
        
        pred_tokens = self._greedy_generate_tokens(test_batch["input_ids"])
        decoded_pred = self.tokenizer.batch_decode(pred_tokens, skip_special_tokens=True)

        decoded_target = [self.tokenizer.decode(tokens[tokens!=-100], skip_special_tokens=True) for tokens in target]
        return {"test_loss_step": test_loss, "pred": decoded_pred, "target": decoded_target}

    def test_epoch_end(self, outputs):
        loss = torch.stack([x['test_loss_step'] for x in outputs]).mean()
        trues = sum([list(x['target']) for x in outputs], [])
        preds = sum([list(x['pred']) for x in outputs], [])

        n = random.choices(range(len(trues)), k=2)
        for i in n:
          print(f"\nSample Target: {trues[i]}\nPrediction: {preds[i]}\n")
        
        f1 = []
        for true, pred in zip(trues, preds):
            f1.append(compute_f1(a_gold=true, a_pred=pred))
        f1_test = np.mean(f1)

        self.log("test_loss", loss, prog_bar=True)
        self.log("test_f1", f1_test, prog_bar=True)

    def configure_optimizers(self):
        
        # optimizer = adafactor.Adafactor(self.parameters(), warmup_init=False,
        #                                 weight_decay=self.hparams["w_decay"])  

        optimizer = torch.optim.Adam(self.parameters(),
                         lr=self.hparams["lr"],
                         weight_decay=self.hparams["w_decay"])
        
        scheduler = LinearWarmupCosineAnnealingLR(optimizer, 
                                                  eta_min=0, # final-lr
                                                  warmup_start_lr=self.hparams["lr"],
                                                  warmup_epochs=self.hparams["hold_epochs"], # hold_epochs
                                                  max_epochs=self.hparams["max_epochs"])
        
        return {'optimizer': optimizer, 'lr_scheduler': scheduler, 'monitor':'val_f1'}
        # return optimizer   

In [ ]:
hparams["lr"]

0.0005

# Defining the BertNet and training

In [ ]:
pl_model= PTT5Net(hparams=hparams)

checkpoint_path = '/content/drive/MyDrive/ptt5_train/epoch=0.ckpt'
checkpoint_dir = os.path.dirname(os.path.abspath(checkpoint_path))
print(f'Files in {checkpoint_dir}: {os.listdir(checkpoint_dir)}')
print(f'Saving checkpoints to {checkpoint_dir}')
checkpoint_callback = pl.callbacks.ModelCheckpoint(prefix=hparams["version"],
                                                    dirpath=checkpoint_dir,
                                                    save_top_k=1, 
                                                    monitor="val_f1", mode="max")
early_stop_callback = pl.callbacks.EarlyStopping(monitor='val_f1', patience=hparams["patience"], mode='max')
lr_monitor = pl.callbacks.LearningRateMonitor(logging_interval='step')


trainer = pl.Trainer(gpus=1, 
                     precision=16,
                     # logger=neptune_logger,
                     # val_check_interval=0.25,
                     num_sanity_val_steps=0,
                     accumulate_grad_batches=hparams["accum_grads"],
                     checkpoint_callback=checkpoint_callback, 
                     callbacks=[early_stop_callback, lr_monitor],
                     max_epochs=hparams["max_epochs"])

/usr/local/lib/python3.7/dist-packages/pytorch_lightning/utilities/distributed.py:68: UserWarning: Checkpoint directory /content/drive/MyDrive/ptt5_train exists and is not empty.
  warnings.warn(*args, **kwargs)
GPU available: True, used: True
TPU available: False, using: 0 TPU cores
Using native 16bit precision.


Files in /content/drive/MyDrive/ptt5_train: ['PTT5_inputmask_oldvocab_test1-epoch=0-step=294.ckpt', 'PTT5_inputmask_oldvocab_test1-epoch=46-step=13864.ckpt', 'PTT5_noise_oldvocab_test1-epoch=49-step=14749.ckpt', 'PTT5_noise_oldvocab_test2-epoch=18-step=5604.ckpt', 'PTT5_noise_oldvocab_adafactor_test1-epoch=0-step=589.ckpt', 'PTT5_noise_oldvocab_adafactor_test2-epoch=3-step=1575.ckpt', 'PTT5_noise_oldvocab_adafactor_test3-epoch=29-step=11819.ckpt', 'PTT5_noise_oldvocab_adafactor_test4-epoch=8-step=3545.ckpt', 'PTT5_noise_oldvocab_adafactor_test5-epoch=12-step=3418.ckpt', 'PTT5_noise_oldvocab_adafactor_test6-epoch=10-step=2892.ckpt', 'PTT5_noise_oldvocab_adafactor_test7-epoch=11-step=3155.ckpt', 'PTT5_noise_oldvocab_adafactor_test6-epoch=1-step=295.ckpt', 'PTT5_noise_oldvocab_adafactor_test7-epoch=13-step=2071.ckpt']
Saving checkpoints to /content/drive/MyDrive/ptt5_train


In [ ]:
trainer.fit(pl_model, train_dataloader, val_dataloader)

LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]

  | Name  | Type                       | Params
-----------------------------------------------------
0 | model | T5ForConditionalGeneration | 222 M 
-----------------------------------------------------
222 M     Trainable params
0         Non-trainable params
222 M     Total params
891.614   Total estimated model params size (MB)



Sample Target: nos dias quentes e ao praticar esportes você deve beber mais
Prediction: nos dias quentes e ao praticar esportes você deve beber mais


Sample Target: uma jovem mulher de topless exceto tinta ou lama
Prediction: uma jovem jovem de tons diferentes exceto tinta ou lama




Sample Target: este aviso isenta a notificação individualizada
Prediction: este aviso é uma notícia duplicada


Sample Target: diferentes gotas para pessoas diferentes
Prediction: diminutas para suas necessidades




Sample Target: não você verificou no balcão
Prediction: não vocêificou o balcão


Sample Target: o egoísmo é um vício tão antigo quanto o mundo
Prediction: o mesmo é um filme tão sintomático quanto o filme




Sample Target: coberto com lona
Prediction: coberto com lona


Sample Target: e eles atacaram uma tenda vazia
Prediction: e eles atacavam uma casa vazia



...


Sample Target: ela diz que não é nada para se preocupar
Prediction: ela diz que não é nada para se preocupar


Sample Target: todo software de processamento de imagens contém contraste automático e aprimoramento de cores
Prediction: todo software de processamento de imagens contém filtro automatizado e analiseamento de cores




Sample Target: para nossos objetivos é claro vamos querer usar um comando de voz
Prediction: para nossos objetivos é claro vamos querer usar um marcador de voz


Sample Target: o menino estava forte e queria retaliar mas ele estava em um país estrangeiro
Prediction: o menino estava triste e queria respirar ar puro ele estava em um país estrangeiro




Sample Target: finalmente aliviado
Prediction: realmente amado


Sample Target: mas finalmente o comerciante apareceu e pediu ao menino para cortar quatro ovelhas
Prediction: mas finalmente o comerciante apareceu e pediu ao menino para cortar quatro ovelhas




Sample Target: esperança não é apenas um esforço unilateral
Prediction: esculpir não é apenas um esforço inacabado


Sample Target: sim foi assim que pensei
Prediction: sim foi assim que pensei




1

# Testing the best model

In [ ]:
# best_model = checkpoint_callback.best_model_path
best_model = '/content/drive/MyDrive/ptt5_train/PTT5_noise_oldvocab_adafactor_test7-epoch=13-step=2071.ckpt'
print(best_model)
test_model = PTT5Net.load_from_checkpoint(best_model, hparams=hparams).cuda().eval()

/content/drive/MyDrive/ptt5_train/PTT5_noise_oldvocab_adafactor_test7-epoch=13-step=2071.ckpt


In [ ]:
trainer.test(test_model, test_dataloader)

LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]



Sample Target: muito melhor disse o velho
Prediction: muito melhor disse o velho


Sample Target: uma pessoa em uma bicicleta de bmx
Prediction: uma pessoa em uma bicicleta de bmx


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_f1': 0.8288804813753453, 'test_loss': 0.6705524921417236}
--------------------------------------------------------------------------------


[{'test_f1': 0.8288804813753453, 'test_loss': 0.6705524921417236}]

#Deploy model to one file to in wav2vec

In [ ]:
# script = test_model.to_torchscript()

PATH = "/content/drive/MyDrive/ptt5_train/PTT5Net_model.pt"

# # save for use in production environment
# torch.jit.save(script, PATH)

torch.save(test_model, PATH)

In [ ]:
model_ptt5 = torch.load(PATH)
model_ptt5.eval()

PTT5Net(
  (model): T5ForConditionalGeneration(
    (shared): Embedding(32128, 768)
    (encoder): T5Stack(
      (embed_tokens): Embedding(32128, 768)
      (block): ModuleList(
        (0): T5Block(
          (layer): ModuleList(
            (0): T5LayerSelfAttention(
              (SelfAttention): T5Attention(
                (q): Linear(in_features=768, out_features=768, bias=False)
                (k): Linear(in_features=768, out_features=768, bias=False)
                (v): Linear(in_features=768, out_features=768, bias=False)
                (o): Linear(in_features=768, out_features=768, bias=False)
                (relative_attention_bias): Embedding(32, 12)
              )
              (layer_norm): T5LayerNorm()
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (1): T5LayerFF(
              (DenseReluDense): T5DenseReluDense(
                (wi): Linear(in_features=768, out_features=3072, bias=False)
                (wo): Linear(in_features=3

In [ ]:
trainer.test(model_ptt5, test_dataloader)

LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]



Sample Target: eu estou aqui há um mês
Prediction: eu estou aqui há um mês


Sample Target: mister robinson chegará a tempo
Prediction: mister bruno chegará a tempo


--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_f1': 0.8265936370701581, 'test_loss': 0.6714709997177124}
--------------------------------------------------------------------------------


[{'test_f1': 0.8265936370701581, 'test_loss': 0.6714709997177124}]

## Greedy 

In [ ]:
y_true = list()
y_pred = list()

for i, batch in enumerate(test_dataloader):
  with torch.no_grad():
    for key in batch.keys():
       batch[key] = batch[key].cuda()
    print('inputs:', tokenizer.decode(batch['input_ids'][0]))   
    preds, targets = test_model.predict_step(batch, i)
  print('---------------------------------------------------')     
  y_pred.append(preds)
  y_true.append(targets)

y_true = np.concatenate(y_true)
y_pred = np.concatenate(y_pred)

Streaming output truncated to the last 5000 lines.

---------------------------------------------------
inputs: dua crianças estã dormindo enqanto lRuém está mxendo em um livro de músiJa</s>

Sample Target: duas crianças estão dormindo enquanto alguém está mexendo em um livro de música
Prediction: duas crianças estão dormindo enquanto alguém está mexendo em um livro de música

---------------------------------------------------
inputs: um arNista montafo um cavalo enquanYo agitanio a bandeira amebicUna e vestinao verde</s>

Sample Target: um artista montando um cavalo enquanto agitando a bandeira americana e vestindo verde
Prediction: um corredor montando um cavalo enquanto agitando a bandeira brasileira e vestindo verde

---------------------------------------------------
inputs: quaduer oomportaTento que possa infringir os diNeiOos do professr</s>

Sample Target: qualquer comportamento que possa infringir os direitos do professor
Prediction: qualquer dispositivo que possa violar os d

In [ ]:
print(y_true[0:5])
print(y_pred[0:5])

['nem o radar nem os outros instrumentos detectaram o bombardeiro stealth'
 'pedir dinheiro emprestado às pessoas da aldeia' 'oito' 'trancálos'
 'realizar uma investigação para resolver o problema']
['nem o governo nem os outros órgãos deram o feedback esperado'
 'pedir dinheiro emprestado às pessoas da cidade' 'oito' 'trancálos'
 'realizar uma investigação para resolver o problema']


In [ ]:
f1 = []
for true, pred in zip(y_true, y_pred):
    f1.append(compute_f1(a_gold=true, a_pred=pred))
f1_test = np.mean(f1)

print('f1:', f1_test)

del y_true, y_pred
torch.cuda.empty_cache()

f1: 0.8267231311827101


## beam-search

In [ ]:
y_true = list()
y_pred = list()

for i, batch in enumerate(test_dataloader):
  with torch.no_grad():
    #for key in batch.keys():
    #  batch[key] = batch[key].cuda()
    # batch['input_ids'] = batch['input_ids'].cuda()
    print('inputs:', tokenizer.decode(batch['input_ids'][0]))  
    preds, targets = test_model.predict_step(batch, i, gen_type=0)   
  print('---------------------------------------------------') 
  y_pred.append(preds)
  y_true.append(targets)
  del preds, targets, batch
  torch.cuda.empty_cache()  

y_true = np.concatenate(y_true)
y_pred = np.concatenate(y_pred)

inputs: nem o radar nem os outros instrucentds detJaHam o bomQarzeiro stealth</s>


/usr/local/lib/python3.7/dist-packages/transformers/generation_beam_search.py:197: UserWarning: Passing `max_length` to BeamSearchScorer is deprecated and has no effect.`max_length` should be passed directly to `beam_search(...)`, `beam_sample(...)`,or `group_beam_search(...)`.
  "Passing `max_length` to BeamSearchScorer is deprecated and has no effect."



Sample Target: nem o radar nem os outros instrumentos detectaram o bombardeiro stealth
Prediction: nem o radar nem os outros instrumentos deram o bombeiro stealth

---------------------------------------------------
inputs: realizar kma inhetGação para resolver o problema</s> <pad> <pad> <pad> <pad> <pad>

Sample Target: realizar uma investigação para resolver o problema
Prediction: realizar uma intervenção para resolver o problema

---------------------------------------------------
inputs: duas mulhFres que Yentamse pJra baiSo lendo jonais</s>

Sample Target: duas mulheres que sentamse para baixo lendo jornais
Prediction: duas mulheres que sentamse para fotos lendo jornais

---------------------------------------------------
inputs: duas muees e uma enina lvantam hom troféus</s> <pad> <pad> <pad> <pad> <pad> <pad> <pad>

Sample Target: duas mulheres e uma menina levantam com troféus
Prediction: duas mulheres e uma menina levantam seus troféus

---------------------------------------

In [ ]:
f1 = []
for true, pred in zip(y_true, y_pred):
    f1.append(compute_f1(a_gold=true, a_pred=pred))
f1_test1 = np.mean(f1)

print('f1:', f1_test1)

del y_true, y_pred
torch.cuda.empty_cache()

## Top K

In [ ]:
y_true = list()
y_pred = list()

for i, batch in enumerate(test_dataloader):
  with torch.no_grad():
    for key in batch.keys():
      batch[key] = batch[key].cuda()
    preds, targets = test_model.predict_step(batch, i, gen_type=2)   
  y_pred.append(preds)
  y_true.append(targets)

y_true = np.concatenate(y_true)
y_pred = np.concatenate(y_pred)

In [ ]:
f1 = []
for true, pred in zip(y_true, y_pred):
    f1.append(compute_f1(a_gold=true, a_pred=pred))
f1_test3 = np.mean(f1)

print('f1:', f1_test3)

del y_true, y_pred
torch.cuda.empty_cache()

# Top-p

In [ ]:
# y_true = list()
# y_pred = list()

# for i, batch in enumerate(test_dataloader):
#   with torch.no_grad():
#     for key in batch.keys():
#       batch[key] = batch[key].cuda()
#     preds, targets = test_model.predict_step(batch, i, gen_type=3)   
#   y_pred.append(preds)
#   y_true.append(targets)

# y_true = np.concatenate(y_true)
# y_pred = np.concatenate(y_pred)

In [ ]:
# f1 = []
# for true, pred in zip(y_true, y_pred):
#     f1.append(compute_f1(a_gold=true, a_pred=pred))
# f1_test3 = np.mean(f1)

# print('f1:', f1_test3)

## Top-p and Top-K 

In [ ]:
y_true = list()
y_pred = list()

for i, batch in enumerate(test_dataloader):
  with torch.no_grad():
    # print(batch)
    for key in batch.keys():
      batch[key] = batch[key].cuda()
    print('inputs:', tokenizer.decode(batch['input_ids'][0]))  
    preds, targets = test_model.predict_step(batch, i, gen_type=4)   
  y_pred.append(preds)
  y_true.append(targets)
  print('--------------------------------------------------')

y_true = np.concatenate(y_true)
y_pred = np.concatenate(y_pred)

Streaming output truncated to the last 5000 lines.

--------------------------------------------------
inputs: duas crinçaf estão dormindo enqGanMp plguém esá mJxendo em um livrr d músiNK</s>

Sample Target: duas crianças estão dormindo enquanto alguém está mexendo em um livro de música
Prediction: duas crianças estão dormindo enquanto alguém está tocando em um livro de música

--------------------------------------------------
inputs: cm artista montcndo um cvao enquato gitando H bandeira amercana e vestindo vardx</s>

Sample Target: um artista montando um cavalo enquanto agitando a bandeira americana e vestindo verde
Prediction: um artista montando um cavalo enquanto gigando a bandeira holandesa e vestindo branco

--------------------------------------------------
inputs: qualquWr comportajenjo que poDsa inmrfgir os direitUs do proTessor</s>

Sample Target: qualquer comportamento que possa infringir os direitos do professor
Prediction: qualquer pessoa que possa invocar os recursos do

In [ ]:
f1 = []
for true, pred in zip(y_true, y_pred):
    f1.append(compute_f1(a_gold=true, a_pred=pred))
f1_test4 = np.mean(f1)

print('f1:', f1_test4)

del y_true, y_pred
torch.cuda.empty_cache()

f1: 0.825909643476082
